In [ ]:
import pandas as pd
import re
import gensim
from gensim.models import Word2Vec
from sklearn.manifold import TSNE
import matplotlib.pyplot as plt
from sklearn.cluster import KMeans
import numpy as np
from sklearn.metrics import silhouette_score, davies_bouldin_score, calinski_harabasz_score

In [ ]:
drive_path = "/content/drive/MyDrive/JobHunt/separated_postings.csv"  # Change this if needed
df = pd.read_csv(drive_path, engine="python", on_bad_lines='skip')

In [ ]:
def preprocess(text):
    text = re.sub(r'\W+', ' ', str(text).lower())  # Remove special characters and lowercase
    return text.split()  # Tokenize

In [ ]:
# Tokenize all job postings
sentences = df.iloc[:, 0].dropna().apply(preprocess).tolist()  # Assuming job postings are in the first column

# WORD 2 VEC

In [ ]:
# Train Word2Vec model
word2vec_model = Word2Vec(sentences, vector_size=100, window=10, min_count=5, workers=4)
word_vectors = word2vec_model.wv

## **UMAP**

In [119]:
from umap import UMAP

# Apply UMAP instead of t-SNE for dimensionality reduction
words = list(word_vectors.index_to_key)
word_embeddings = np.array([word_vectors[word] for word in words])

umap = UMAP(n_components=2, random_state=42)
word_embeddings_2d = umap.fit_transform(word_embeddings)

/usr/local/lib/python3.11/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/usr/local/lib/python3.11/dist-packages/umap/umap_.py:1952: UserWarning: n_jobs value 1 overridden to 1 by setting random_state. Use no seed for parallelism.
  warn(


# CLUSTERING. CHANGE ALGO HERE. ENSURE CLUSTER NAME IS 'clusters'

In [206]:
from sklearn.cluster import SpectralClustering

# Apply Spectral Clustering with optimized parameters
num_clusters = 10  # Desired number of clusters
spectral = SpectralClustering(n_clusters=num_clusters, affinity='nearest_neighbors', n_neighbors=10, random_state=42)
clusters = spectral.fit_predict(word_embeddings_2d)

/usr/local/lib/python3.11/dist-packages/sklearn/manifold/_spectral_embedding.py:329: UserWarning: Graph is not fully connected, spectral embedding may not work as expected.
  warnings.warn(


In [212]:
import matplotlib.pyplot as plt
import numpy as np

# Get the unique cluster labels (excluding noise, if present)
cluster_ids = np.unique(clusters)
# Filter out noise cluster if it exists (cluster -1)
cluster_ids = cluster_ids[cluster_ids != -1]

# Define the fixed colors for each cluster ID
cluster_colors = np.unique(clusters)
num_clusters = len(cluster_colors)

# Create a color map with specific colors for each cluster
cmap = plt.get_cmap("tab10", num_clusters)  # Using tab10 to match with cluster count
norm = BoundaryNorm(np.arange(num_clusters + 1) - 0.5, num_clusters)

plt.figure(figsize=(12, 8))

# Scatter plot with aligned colors
scatter = plt.scatter(word_embeddings_2d[:, 0], word_embeddings_2d[:, 1],
                     c=clusters, cmap=cmap, norm=norm, s=10, alpha=0.6)  # Aligned colors

# Plot noise points separately (if present)
noise_indices = np.where(clusters == -1)[0]
if len(noise_indices) > 0:
    plt.scatter(word_embeddings_2d[noise_indices, 0],
                word_embeddings_2d[noise_indices, 1],
                c="gray", label="Noise")  # Assign gray color to noise points

plt.title("Word Clusters using Word2Vec, UMAP, and Spectral Clustering")
plt.legend()  # Show legend to identify clusters
plt.show()

<ipython-input-212-c278efe8ffa5>:31: UserWarning: No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
  plt.legend()  # Show legend to identify clusters


# METRICS

In [213]:
# Compute internal evaluation metrics
silhouette_avg = silhouette_score(word_embeddings_2d, clusters)
davies_bouldin = davies_bouldin_score(word_embeddings_2d, clusters)
calinski_harabasz = calinski_harabasz_score(word_embeddings_2d, clusters)

print("\nClustering Evaluation Metrics:")
print(f"Silhouette Score: {silhouette_avg:.4f} (Higher is better)")
print(f"Davies-Bouldin Index: {davies_bouldin:.4f} (Lower is better)")
print(f"Calinski-Harabasz Index: {calinski_harabasz:.4f} (Higher is better)")

# Visualization with aligned colors
plt.figure(figsize=(12, 8))

# Get the unique cluster labels (excluding noise, if present)
cluster_ids = np.unique(clusters)
# Filter out noise cluster if it exists (cluster -1)
cluster_ids = cluster_ids[cluster_ids != -1]

# Define the fixed colors for each cluster ID
cluster_colors = np.unique(clusters)
num_clusters = len(cluster_colors)

# Create a color map with specific colors for each cluster
cmap = plt.get_cmap("tab10", num_clusters)  # Using tab10 to match with cluster count
norm = BoundaryNorm(np.arange(num_clusters + 1) - 0.5, num_clusters)


# Scatter plot with aligned colors
scatter = plt.scatter(word_embeddings_2d[:, 0], word_embeddings_2d[:, 1],
                     c=clusters, cmap=cmap, norm=norm, s=10, alpha=0.6)  # Aligned colors


plt.title("Word Clusters using Word2Vec, UMAP, and Spectral Clustering")
plt.show()


Clustering Evaluation Metrics:
Silhouette Score: 0.3266 (Higher is better)
Davies-Bouldin Index: 0.7268 (Lower is better)
Calinski-Harabasz Index: 9591.8612 (Higher is better)


# Get first 100 worsds on each cluster

In [209]:
# Get the unique cluster labels (excluding noise, if present)
cluster_ids = np.unique(clusters)
# Filter out noise cluster if it exists (cluster -1)
cluster_ids = cluster_ids[cluster_ids != -1]

# Create a dictionary to store words for each cluster
clustered_words = {}

# Iterate through the unique cluster IDs
for cluster_id in cluster_ids:
    indices = np.where(clusters == cluster_id)[0]
    sampled_indices = np.random.choice(indices, min(100, len(indices)), replace=False)
    clustered_words[cluster_id] = [words[i] for i in sampled_indices]

# Print sampled words per cluster
for cluster_id, word_list in clustered_words.items():
    print(f"\nCluster {cluster_id}:")
    print(", ".join(word_list))


Cluster 0:
gloves, log, logic, indoor, layout, accurately, api, vents, observe, structural, javascript, scripts, pneumatic, equipment, monitors, items, audiovisual, chain, engineer, photolithography, pound, estimates, acuity, buildings, noisy, talk, testing, libraries, desktop, cloud, ot, specimens, manufacturers, blueprints, overview, exempt, phones, blade, pull, accounting, h, crawls, technical, collections, water, intermediate, modifications, expense, tracks, instruments, lbs, designer, necessary, mp, integration, replacement, advanced, deployments, ux, pv, spaces, edge, assistant, crane, eg, mathematics, perform, trace, abnormal, squatting, approve, periods, reconcile, film, damage, timely, receipts, minimize, qa, facilities, structures, steam, r, sanitation, enable, orders, trash, specifications, quick, places, mail, configuration, weather, occasional, printer, rooms, shoes, engines, disposal, read

Cluster 1:
labor_relations, analyzer, sisters, 54460, technical_recruiting, broad

# Find words on the clusters

In [210]:
def annotate_words(word_list, word_vectors, word_embeddings_2d):
    """Annotate specific words on the scatter plot."""
    for word in word_list:
        if word in word_vectors.key_to_index:  # Check if the word exists in vocabulary
            idx = word_vectors.key_to_index[word]  # Get index directly from Word2Vec
            plt.annotate(word, (word_embeddings_2d[idx, 0], word_embeddings_2d[idx, 1]),
                         fontsize=9, color='black', ha='right')

## ANNOTATE TECH

In [211]:
import matplotlib.pyplot as plt
import matplotlib.patheffects as path_effects
import numpy as np
from matplotlib.colors import BoundaryNorm

fig, axes = plt.subplots(2, 3, figsize=(24, 16))
fig.suptitle('Word Clusters using Word2Vec and UMAP with Skill Related Words', fontsize=16)

# List of data for each subplot
data = [
    (['Advertising', 'Art', 'Creative', 'Design', 'Distribution', 'Consulting', 'Analyst', 'Health', 'Care', 'science',
      'mathematics', 'legal', 'quality', 'information', 'relations', 'writing', 'editing', 'accounting', 'auditing',
      'manufacturing', 'sales', 'management', 'marketing', 'production', 'administrative', 'research', 'quality',
      'strategy', 'planning', 'purchasing', 'training', 'human_resources'], 'Skills'),
    (['technology', 'business', 'medicine', 'law', 'engineering', 'retail', 'food', 'apparel', 'entertainment', 'gambling',
      'design', 'investment', 'education', 'logistics', 'advertisement', 'beverage', 'natural', 'automotive', 'security',
      'ai', 'blockchain', 'defence', 'computer', 'hardware', 'software', 'development', 'semiconductor',
      'telecommunications', 'consulting', 'biotechnology', 'pharmaceutical', 'veterinary', 'fashion', 'sport',
      'sporting', 'electronics', 'furniture', 'travel', 'restaurants', 'recreational', 'insurance', 'estate',
      'construction', 'architecture', 'civil', 'aviation', 'motor', 'mining', 'utilities', 'farming', 'agriculture',
      'fisheries', 'forces', 'international', 'affairs', 'safety', 'printing'], 'Industry'),
    (['remote_yes', 'remote_no'], 'Remoteness'),
    (['hourly', 'yearly', 'monthly'], 'Pay Period'),
    (['medical_insurance', 'vision_insurance', 'tuition_assistance', '401_(k)', 'dental_insurance',
      'student_loan_assistance', 'disabililty_insurance', 'child_care_support', 'commuter_benefits',
      'paid_paternity_leave'], 'Benefits'),
    (['ibm', 'accenture', 'oracle', 'microsoft', 'cisco', 'nxp', 'pfizer', 'atos', 'honeywell', 'pepsiCo',
      'carestream', 'amazon', 'rbc', 'oracle', 'ge_healthcare', 'hawlett_packard_enterprise', 'bt_group', 'atos',
      'boeing', 'adobe', 'sanofi', 'harvard_university', 'aig', 'charles_schwab', 'medtronic', 'ups'], 'Company')
]

# Define the fixed colors for each cluster ID
cluster_colors = np.unique(clusters)
num_clusters = len(cluster_colors)

# Create a color map with specific colors for each cluster
cmap = plt.get_cmap("tab10", num_clusters)  # Using tab10 to match with cluster count
norm = BoundaryNorm(np.arange(num_clusters + 1) - 0.5, num_clusters)

# Plot each set of annotations
for ax, (annotations, title) in zip(axes.flat, data):
    scatter = ax.scatter(word_embeddings_2d[:, 0], word_embeddings_2d[:, 1],
                         c=clusters, cmap=cmap, norm=norm, s=10, alpha=0.6)
    ax.set_title(title)
    for word in annotations:
        if word in word_vectors.key_to_index:
            idx = word_vectors.key_to_index[word]
            x, y = word_embeddings_2d[idx]
            txt = ax.text(x, y, word, fontsize=8, weight='bold', color='black')
            txt.set_path_effects([path_effects.Stroke(linewidth=2, foreground='white'), path_effects.Normal()])

# Adjust layout to fit the color bar below the title
fig.subplots_adjust(top=0.85, bottom=0.09, left=0.05, right=0.95, hspace=0.3, wspace=0.2)

# Add a horizontal color bar below the title and above the subplots
cbar_ax = fig.add_axes([0.3, 0.91, 0.4, 0.03])  # [left, bottom, width, height]
cbar = fig.colorbar(scatter, cax=cbar_ax, orientation='horizontal', ticks=range(num_clusters))
cbar.set_label('Cluster ID')
cbar.ax.set_xticklabels([str(i) for i in range(num_clusters)])

plt.show()
